## EV VPP simulator for SB3 trained model (Maskable PPO)

Installing required packages and dependencies

In [ ]:
%%capture
!pip install py-elvis
!pip install pyyaml==5.4
!pip install plotly==5.9.0
!pip install -U kaleido

!pip install stable-baselines3[extra]
!pip install stable-baselines
!pip install sb3-contrib
!pip install gym
!pip install -q wandb

In [ ]:
#Cloning repository and changing directory
!git clone https://github.com/francescomaldonato/RL_VPP_Thesis.git
%cd RL_VPP_Thesis/
%ls

In [ ]:
import yaml
import numpy as np
from gym import Env
from VPP_environment import VPPEnv, VPP_Scenario_config
from elvis.config import ScenarioConfig
import os
import torch
import random
import wandb
from sb3_contrib import RecurrentPPO #The available algoritmhs in sb3-contrib for the custom environment with MultiInputPolicy
from sb3_contrib.common.maskable.utils import get_action_masks
import stable_baselines3 as sb3
from stable_baselines3.common.env_checker import check_env

#Check if cuda device is available for training
print("Torch-Cuda available device:", torch.cuda.is_available())
print(sb3.get_system_info())
!wandb --version

Torch-Cuda available device: False
OS: Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022
Python: 3.7.14
Stable-Baselines3: 1.6.1
PyTorch: 1.12.1+cu113
GPU Enabled: False
Numpy: 1.21.6
Gym: 0.21.0

({'OS': 'Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022', 'Python': '3.7.14', 'Stable-Baselines3': '1.6.1', 'PyTorch': '1.12.1+cu113', 'GPU Enabled': 'False', 'Numpy': '1.21.6', 'Gym': '0.21.0'}, 'OS: Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022\nPython: 3.7.14\nStable-Baselines3: 1.6.1\nPyTorch: 1.12.1+cu113\nGPU Enabled: False\nNumpy: 1.21.6\nGym: 0.21.0\n')
wandb, version 0.13.3


In [ ]:
# Ensure deterministic behavior
torch.backends.cudnn.deterministic = True
random.seed(0)
torch.manual_seed(0)
torch.cuda.manual_seed_all(0)

In [ ]:
#Loading paths for input data
current_folder = ''
VPP_training_data_input_path = current_folder + 'data/data_training/environment_table/' + 'Environment_data_2019.csv'
VPP_testing_data_input_path = current_folder + 'data/data_testing/environment_table/' + 'Environment_data_2020.csv'
VPP_validating_data_input_path = current_folder + 'data/data_validating/environment_table/' + 'Environment_data_2018.csv'
elvis_input_folder = current_folder + 'data/config_builder/'

case = 'wohnblock_household_simulation_adaptive.yaml'
with open(elvis_input_folder + case, 'r') as file:
    yaml_str = yaml.full_load(file)

elvis_config_file = ScenarioConfig.from_yaml(yaml_str)
VPP_config_file = VPP_Scenario_config(yaml_str)

print(elvis_config_file)
print(VPP_config_file)

Vehicle types: <generator object ScenarioConfig.__str__.<locals>.<genexpr> at 0x7fb86c838850>Mean parking time: 23.9
Std deviation of parking time: 1
Mean value of the SOC distribution: 0.5
Std deviation of the SOC distribution: 0.1
Max parking time: 24
Number of charging events per week: 20
Vehicles are disconnected only depending on their parking time
Queue length: 0
Opening hours: None
Scheduling policy: Uncontrolled

{'start_date': '2022-01-01T00:00:00', 'end_date': '2023-01-01T00:00:00', 'resolution': '0:15:00', 'num_households': 4, 'solar_power': 16, 'wind_power': 12, 'EV_types': [{'battery': {'capacity': 100, 'efficiency': 1, 'max_charge_power': 150, 'min_charge_power': 0}, 'brand': 'Tesla', 'model': 'Model S', 'probability': 1}], 'charging_stations_n': 4, 'EVs_n': 20, 'EVs_n_max': 1044, 'mean_park': 23.9, 'std_deviation_park': 1, 'EVs_mean_soc': 50.0, 'EVs_std_deviation_soc': 10.0, 'EV_load_max': 44, 'EV_load_rated': 14.8, 'EV_load_min': 1, 'houseRWload_max': 10, 'av_max_energy

In [ ]:
#TESTING Environment initialization
env = VPPEnv(VPP_testing_data_input_path, elvis_config_file, VPP_config_file)
env.plot_VPP_input_data()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_ELVIS_data()

In [ ]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
env.plot_reward_functions()

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  22152.29 , over-consume=kWh  39199.89 , under-consume=kWh  17047.6 , Total_cost=€  894.72 , overcost=€  1388.09 , Av.EV_en_left=kWh  100.0 , Charging_events=  1043 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  75.08
Simulating VPP....


### VPP Simulation test with random actions [no model loaded]

In [ ]:
episodes = 1
for episode in range(1, episodes+1):
    state = env.reset()
    done = False
    score = 0
    while not done:
        action_masks = get_action_masks(env)
        action = env.action_space.sample()
        
        n_state, reward, done, info = env.step(action)
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_Elvis_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_VPP_Elvis_comparison()

In [ ]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_rewards_stats()

In [ ]:
env.plot_EVs_kpi()

In [ ]:
env.plot_actions_kpi()

In [ ]:
env.plot_load_kpi()

In [ ]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
## Wandb login to load models
#In Colab, uncomment below:
%env "WANDB_DISABLE_CODE" True
%env "WANDB_NOTEBOOK_NAME" "Simulator_notebooks/RecurrentPPO_VPP_simulator.ipynb"
os.environ['WANDB_NOTEBOOK_NAME'] = 'Simulator_notebooks/RecurrentPPO_VPP_simulator.ipynb'
#wandb.login(relogin=True)

#In local notebook, uncomment below:
#your_wandb_login_code = 0123456789abcdefghijklmnopqrstwxyzàèìòù0 #example length
#!wandb login {your_wandb_login_code}

env: "WANDB_DISABLE_CODE"=True
env: "WANDB_NOTEBOOK_NAME"="Simulator_notebooks/RecurrentPPO_VPP_simulator.ipynb"


In [ ]:
#Loading training model, from local directory or from wandb previous trainings
RecurrentPPO_path = "trained_models/RecurrentPPO_models/model_RecurrentPPO_"

model_id = "s37o8q0n"
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

# run_id_restore = "2y2dqvyn"
# model = wandb.restore(f'model_{run_id_restore}.zip', run_path=f"francesco_maldonato/RL_VPP_Thesis/{run_id_restore}")

/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



## Testing dataset VPP Simulation using the loaded trained model

In [ ]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  21473.48 , over-consume=kWh  38785.43 , under-consume=kWh  17311.96 , Total_cost=€  887.38 , overcost=€  1380.23 , Av.EV_en_left=kWh  100.0 , Charging_events=  1043 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  75.08
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -4964.93 , over-consume=KWh  1733.1 , under-consume=KWh  6698.03 , Total_cost=€  -112.97 , Overcost=€  63.08 
 EV_INFO: Av.EV_energy_leaving=kWh  65.82 , Std.EV_energy_leaving=kWh  26.95 , EV_departures =  1043 , EV_queue_left =  0
SCORE:  Cumulative_reward= 379008.88 - Step_rewars (load_t= 353536.33, EVs_energy_t= 3437.02)
 - Final_rewards (EVs_energy= 15231.54, Overconsume= -1007.52, Underconsume= -3504.42, Overcost= 11315.95)
Episode:1 Score:379008.8835324622


In [ ]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
VPP_table.head(15000)

0          1          2          3  \
time                                                              
2022-01-01 00:00:00  72.662804  53.062515  41.732056  57.181679   
2022-01-01 00:15:00  72.072449  53.312515  41.982056  56.591324   
2022-01-01 00:30:00  71.535141  53.562515  42.232056  56.054012   
2022-01-01 00:45:00  71.117805  53.812515  42.482056  55.636677   
2022-01-01 01:00:00  70.682640  54.062515  42.732056  55.201511   
...                        ...        ...        ...        ...   
2022-06-06 04:45:00  35.239075  57.417786  99.989998  58.054123   
2022-06-06 05:00:00  35.239075  58.384003  99.989998  59.020340   
2022-06-06 05:15:00  35.239075  59.323059  99.989998  59.959396   
2022-06-06 05:30:00  35.239075  60.349133  99.989998  60.985470   
2022-06-06 05:45:00  35.239075  61.407928  99.989998  62.044266   

                                       EVs_id       actions  \
time                                                          
2022-01-01 00:00:00              [0, 0, 0, 0]  [2, 1, 1, 2]   
2022-01-01 00:15:00  [3129, 3128, 3127, 3126]  [2, 1, 1, 2]   
2022-01-01 00:30:00  [3129, 3128, 3127, 3126]  [2, 1, 1, 2]   
2022-01-01 00:45:00  [3129, 3128, 3127, 3126]  [2, 1, 1, 2]   
2022-01-01 01:00:00  [3129, 3128, 3127, 3126]  [2, 1, 1, 2]   
...                                       ...           ...   
2022-06-06 04:45:00  [3591, 3593, 3590, 3592]  [0, 1, 1, 1]   
2022-06-06 05:00:00  [3591, 3593, 3590, 3592]  [0, 1, 1, 1]   
2022-06-06 05:15:00  [3591, 3593, 3590, 3592]  [0, 1, 1, 1]   
2022-06-06 05:30:00  [3591, 3593, 3590, 3592]  [0, 1, 1, 1]   
2022-06-06 05:45:00  [3591, 3593, 3590, 3592]  [0, 1, 1, 1]   

                                       mask_truth          load  load_reward  \
time                                                                           
2022-01-01 00:00:00  [False, False, False, False]  1.909398e+00    15.000000   
2022-01-01 00:15:00    [True, False, False, True]  0.000000e+00    15.000000   
2022-01-01 00:30:00    [True, False, False, True]  0.000000e+00    15.000000   
2022-01-01 00:45:00    [True, False, False, True]  0.000000e+00    15.000000   
2022-01-01 01:00:00    [True, False, False, True]  2.220446e-16    15.000000   
...                                           ...           ...          ...   
2022-06-06 04:45:00    [False, True, False, True] -2.799681e+00    -4.774768   
2022-06-06 05:00:00    [False, True, False, True] -3.864861e+00    -4.593696   
2022-06-06 05:15:00    [False, True, False, True] -3.756218e+00    -5.094804   
2022-06-06 05:30:00    [False, True, False, True] -4.104284e+00    -5.213800   
2022-06-06 05:45:00    [False, True, False, True] -4.235180e+00    -4.888746   

                     EV_reward    rewards  
time                                       
2022-01-01 00:00:00        0.0  15.000000  
2022-01-01 00:15:00        0.0  15.000000  
2022-01-01 00:30:00        0.0  15.000000  
2022-01-01 00:45:00        0.0  15.000000  
2022-01-01 01:00:00        0.0  15.000000  
...                        ...        ...  
2022-06-06 04:45:00        0.0  -4.774768  
2022-06-06 05:00:00        0.0  -4.593696  
2022-06-06 05:15:00        0.0  -5.094804  
2022-06-06 05:30:00        0.0  -5.213800  
2022-06-06 05:45:00        0.0  -4.888746  

[15000 rows x 11 columns]

In [ ]:
env.plot_Elvis_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_VPP_Elvis_comparison()

In [ ]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_rewards_stats()

In [ ]:
env.plot_EVs_kpi()

In [ ]:
env.plot_load_kpi()

In [ ]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

## Validating dataset VPP Simulation using the loaded trained model

In [ ]:
#VALIDATING Environment initialization
env = VPPEnv(VPP_validating_data_input_path, elvis_config_file, VPP_config_file)

Charging event: 4173, Arrival time: 2022-01-01 19:15:00, Parking_time: 24, Leaving_time: 2022-01-02 19:15:00, SOC: 0.5864134300226165, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 5215, Arrival time: 2022-12-31 14:45:00, Parking_time: 24, Leaving_time: 2023-01-01 14:45:00, SOC: 0.5019672918726107, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -30085.39 , over-consume=kWh  2136.67 , under-consume=kWh  -32222.06 , Total_cost=€  -1187.15 , overcost=€  113.34
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  11878.93 , over-consume=kWh  34157.72 , under-consume=kWh  22278.79 , Total_cost=€  622.96 , overcost=€  1511.03 , Charging_events=  1043 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  80.89


In [ ]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
plot_VPP_input_data = env.plot_VPP_input_data()
plot_VPP_input_data.show()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
#model = PPO.load(PPO_path + model_run_ID, env = env)
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



In [ ]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  12375.32 , over-consume=kWh  34757.87 , under-consume=kWh  22382.55 , Total_cost=€  602.22 , overcost=€  1516.17 , Av.EV_en_left=kWh  100.0 , Charging_events=  1043 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  80.89
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -7350.62 , over-consume=KWh  1126.35 , under-consume=KWh  8476.97 , Total_cost=€  -279.16 , Overcost=€  49.12 
 EV_INFO: Av.EV_energy_leaving=kWh  71.67 , Std.EV_energy_leaving=kWh  25.29 , EV_departures =  1041 , EV_queue_left =  0
SCORE:  Cumulative_reward= 387019.23 - Step_rewars (load_t= 337566.3, EVs_energy_t= 21414.55)
 - Final_rewards (EVs_energy= 18051.95, Overconsume= -506.35, Underconsume= -3351.21, Overcost= 13843.99)
Episode:1 Score:387019.23070946464


In [ ]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
VPP_table.head(15000)

0          1    2          3  \
time                                                        
2022-01-01 00:00:00   0.000000   0.000000  0.0   0.000000   
2022-01-01 00:15:00   0.000000   0.000000  0.0   0.000000   
2022-01-01 00:30:00   0.000000   0.000000  0.0   0.000000   
2022-01-01 00:45:00   0.000000   0.000000  0.0   0.000000   
2022-01-01 01:00:00   0.000000   0.000000  0.0   0.000000   
...                        ...        ...  ...        ...   
2022-06-06 04:45:00  83.214760  55.161819  0.0  61.719704   
2022-06-06 05:00:00  85.088684  54.911819  0.0  63.593628   
2022-06-06 05:15:00  86.955971  54.661819  0.0  65.460915   
2022-06-06 05:30:00  88.920685  54.411819  0.0  67.425629   
2022-06-06 05:45:00  90.686722  54.161819  0.0  69.191666   

                                    EVs_id       actions  \
time                                                       
2022-01-01 00:00:00           [0, 0, 0, 0]  [1, 1, 1, 0]   
2022-01-01 00:15:00           [0, 0, 0, 0]  [1, 1, 1, 0]   
2022-01-01 00:30:00           [0, 0, 0, 0]  [0, 1, 0, 0]   
2022-01-01 00:45:00           [0, 0, 0, 0]  [0, 1, 0, 0]   
2022-01-01 01:00:00           [0, 0, 0, 0]  [0, 1, 0, 0]   
...                                    ...           ...   
2022-06-06 04:45:00  [6722, 6720, 0, 6721]  [1, 2, 2, 1]   
2022-06-06 05:00:00  [6722, 6720, 0, 6721]  [1, 2, 2, 1]   
2022-06-06 05:15:00  [6722, 6720, 0, 6721]  [1, 2, 2, 1]   
2022-06-06 05:30:00  [6722, 6720, 0, 6721]  [1, 2, 2, 1]   
2022-06-06 05:45:00  [6722, 6720, 0, 6721]  [1, 2, 2, 1]   

                                      mask_truth      load  load_reward  \
time                                                                      
2022-01-01 00:00:00  [False, False, False, True] -3.490276    -4.520644   
2022-01-01 00:15:00  [False, False, False, True] -3.712387    -3.348552   
2022-01-01 00:30:00    [True, False, True, True] -3.009131    -2.645991   
2022-01-01 00:45:00    [True, False, True, True] -2.587595    -5.395999   
2022-01-01 01:00:00    [True, False, True, True] -4.435599    -5.169365   
...                                          ...       ...          ...   
2022-06-06 04:45:00   [True, False, False, True]  0.000000    15.000000   
2022-06-06 05:00:00   [True, False, False, True]  0.000000    15.000000   
2022-06-06 05:15:00   [True, False, False, True]  0.000000    15.000000   
2022-06-06 05:30:00   [True, False, False, True]  0.000000    15.000000   
2022-06-06 05:45:00   [True, False, False, True]  0.000000    15.000000   

                     EV_reward    rewards  
time                                       
2022-01-01 00:00:00        0.0  -4.520644  
2022-01-01 00:15:00        0.0  -3.348552  
2022-01-01 00:30:00        0.0  -2.645991  
2022-01-01 00:45:00        0.0  -5.395999  
2022-01-01 01:00:00        0.0  -5.169365  
...                        ...        ...  
2022-06-06 04:45:00        0.0  15.000000  
2022-06-06 05:00:00        0.0  15.000000  
2022-06-06 05:15:00        0.0  15.000000  
2022-06-06 05:30:00        0.0  15.000000  
2022-06-06 05:45:00        0.0  15.000000  

[15000 rows x 11 columns]

In [ ]:
env.plot_VPP_results()


Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_VPP_Elvis_comparison()

In [ ]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_rewards_stats()

In [ ]:
env.plot_EVs_kpi()

In [ ]:
env.plot_load_kpi()

In [ ]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

## Training dataset VPP Simulation using the loaded trained model

In [ ]:
#TRAINING Environment initialization
env = VPPEnv(VPP_training_data_input_path, elvis_config_file, VPP_config_file)

Charging event: 7302, Arrival time: 2022-01-01 10:15:00, Parking_time: 23.78299030178625, Leaving_time: 2022-01-02 10:01:58.765086, SOC: 0.6347715395874028, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 8344, Arrival time: 2022-12-31 22:00:00, Parking_time: 23.444565473688364, Leaving_time: 2023-01-01 21:26:40.435705, SOC: 0.41815802392349544, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -34117.7 , over-consume=kWh  1556.25 , under-consume=kWh  -35673.95 , Total_cost=€  -1196.64 , overcost=€  97.86
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  7816.96 , over-consume=kWh  31040.29 , under-consume=kWh  23223.33 , Total_cost=€  447.98 , overcost=€  1301.12 , Charging_events=  1043 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  84.2


In [ ]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
plot_VPP_input_data = env.plot_VPP_input_data()
plot_VPP_input_data.show()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
#model = PPO.load(PPO_path + model_run_ID, env = env)
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



In [ ]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  7661.5 , over-consume=kWh  31814.87 , under-consume=kWh  24153.37 , Total_cost=€  470.62 , overcost=€  1348.94 , Av.EV_en_left=kWh  100.0 , Charging_events=  1043 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  84.2
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -9880.49 , over-consume=KWh  914.69 , under-consume=KWh  10795.18 , Total_cost=€  -338.33 , Overcost=€  38.69 
 EV_INFO: Av.EV_energy_leaving=kWh  73.46 , Std.EV_energy_leaving=kWh  25.23 , EV_departures =  1043 , EV_queue_left =  0
SCORE:  Cumulative_reward= 359438.49 - Step_rewars (load_t= 308499.17, EVs_energy_t= 23934.85)
 - Final_rewards (EVs_energy= 17441.18, Overconsume= -357.15, Underconsume= -4630.18, Overcost= 14550.62)
Episode:1 Score:359438.491383576


In [ ]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
VPP_table.head(14995)

0          1          2          3  \
time                                                             
2022-01-01 00:00:00   0.00000   0.000000   0.000000   0.000000   
2022-01-01 00:15:00   0.00000   0.000000   0.000000   0.000000   
2022-01-01 00:30:00   0.00000  48.600845   0.000000   0.000000   
2022-01-01 00:45:00   0.00000  49.431618   0.000000   0.000000   
2022-01-01 01:00:00   0.00000  50.811089   0.000000   0.000000   
...                       ...        ...        ...        ...   
2022-06-06 03:30:00  61.41713   0.000000  84.833336  50.438042   
2022-06-06 03:45:00  61.16713   0.000000  85.522827  51.127533   
2022-06-06 04:00:00  60.91713   0.000000  86.518494  52.123199   
2022-06-06 04:15:00  60.66713   0.000000  87.503761  53.108463   
2022-06-06 04:30:00  60.41713   0.000000  88.468666  54.073364   

                                    EVs_id       actions  \
time                                                       
2022-01-01 00:00:00           [0, 0, 0, 0]  [1, 1, 1, 0]   
2022-01-01 00:15:00           [0, 0, 0, 0]  [1, 1, 0, 0]   
2022-01-01 00:30:00        [0, 9388, 0, 0]  [0, 1, 0, 2]   
2022-01-01 00:45:00        [0, 9388, 0, 0]  [0, 1, 0, 0]   
2022-01-01 01:00:00        [0, 9388, 0, 0]  [0, 1, 0, 0]   
...                                    ...           ...   
2022-06-06 03:30:00  [9832, 0, 9831, 9833]  [2, 0, 1, 1]   
2022-06-06 03:45:00  [9832, 0, 9831, 9833]  [2, 0, 1, 1]   
2022-06-06 04:00:00  [9832, 0, 9831, 9833]  [2, 0, 1, 1]   
2022-06-06 04:15:00  [9832, 0, 9831, 9833]  [2, 0, 1, 1]   
2022-06-06 04:30:00  [9832, 0, 9831, 9833]  [1, 0, 1, 1]   

                                      mask_truth      load  load_reward  \
time                                                                      
2022-01-01 00:00:00  [False, False, False, True] -3.253877    -4.634519   
2022-01-01 00:15:00   [False, False, True, True] -3.780712    -3.411740   
2022-01-01 00:30:00    [True, True, True, False] -3.047044    15.000000   
2022-01-01 00:45:00     [True, True, True, True]  0.000000    15.000000   
2022-01-01 01:00:00     [True, True, True, True]  0.000000    15.000000   
...                                          ...       ...          ...   
2022-06-06 03:30:00    [False, True, True, True]  0.000000    15.000000   
2022-06-06 03:45:00    [False, True, True, True]  0.000000    15.000000   
2022-06-06 04:00:00    [False, True, True, True]  0.000000    15.000000   
2022-06-06 04:15:00    [False, True, True, True]  0.000000    15.000000   
2022-06-06 04:30:00     [True, True, True, True]  0.000000    15.000000   

                     EV_reward    rewards  
time                                       
2022-01-01 00:00:00        0.0  -4.634519  
2022-01-01 00:15:00        0.0  -3.411740  
2022-01-01 00:30:00        0.0  15.000000  
2022-01-01 00:45:00        0.0  15.000000  
2022-01-01 01:00:00        0.0  15.000000  
...                        ...        ...  
2022-06-06 03:30:00        0.0  15.000000  
2022-06-06 03:45:00        0.0  15.000000  
2022-06-06 04:00:00        0.0  15.000000  
2022-06-06 04:15:00        0.0  15.000000  
2022-06-06 04:30:00        0.0  15.000000  

[14995 rows x 11 columns]

In [ ]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_VPP_Elvis_comparison()

In [ ]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_rewards_stats()

In [ ]:
env.plot_EVs_kpi()

In [ ]:
env.plot_actions_kpi()

In [ ]:
env.plot_load_kpi()

In [ ]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
#env.close()